- Modificações dessa versão:
 - TODO - mudar variável tirando "admitido mesmo ano de criação" e criar variável "new_firm"


# Configurando o ambiente

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import basedosdados as bd
import pyodbc
import re
import time

sns.set(rc={'figure.figsize':(11.7,8.27)})
sns.set_theme(style="darkgrid")

# Criando lista Odebrecht e Camargo

In [2]:
ode_cam = pd.read_csv("Dados/Input/220414_empresas_valor_grandes_grupos.csv", sep = ";", dtype ='str',  encoding='latin-1')

In [3]:
ode_cam.head()

empresa      grupo  \
0                     Nordeste Quimica S.A. Norquisa  odebrecht   
1            Odebrecht Serviços e Participações S.A.  odebrecht   
2                                        ODBINV S.A.  odebrecht   
3          Odebrecht Participações e Engenharia S.A.  odebrecht   
4  Odebrecht Realizações Imobiliárias e Participa...  odebrecht   

                 cnpj   ano  
0  15.659.535/0001-46  2015  
1  10.904.193/0001-69  2015  
2  15.105.588/0001-15  2015  
3  17.851.495/0001-65  2015  
4  06.206.132/0001-50  2015

In [4]:
ode_cam["cnpj_limpo"] = ode_cam["cnpj"].apply(lambda x: re.sub('[^0-9]', '', str(x)[:10]))

In [5]:
ode_cam.head(10)

empresa      grupo  \
0                     Nordeste Quimica S.A. Norquisa  odebrecht   
1            Odebrecht Serviços e Participações S.A.  odebrecht   
2                                        ODBINV S.A.  odebrecht   
3          Odebrecht Participações e Engenharia S.A.  odebrecht   
4  Odebrecht Realizações Imobiliárias e Participa...  odebrecht   
5         Odebrecht Agroindustrial Investimentos S.A  odebrecht   
6                              Odebrecht Energia S.A  odebrecht   
7                                       Braskem S.A.  odebrecht   
8         Enseada indústria Naval Participações S.A.  odebrecht   
9                                     Odebrecht S.A.  odebrecht   

                 cnpj   ano cnpj_limpo  
0  15.659.535/0001-46  2015   15659535  
1  10.904.193/0001-69  2015   10904193  
2  15.105.588/0001-15  2015   15105588  
3  17.851.495/0001-65  2015   17851495  
4  06.206.132/0001-50  2015   06206132  
5                 NaN  2015             
6  13.079.757/0002-45  2015   13079757  
7  42.150.391/0001-70  2015   42150391  
8  12.243.301/0001-25  2015   12243301  
9  05.144.757/0005-04  2015   05144757

In [6]:
len(ode_cam["cnpj_limpo"])

468

In [7]:
ode_cam = ode_cam.dropna()

In [8]:
len(ode_cam)

292

In [9]:
ode_cam.to_csv("Dados/Output/220413_cnpjs_odebrecht_camargo.csv", sep = ";", index = False, encoding = "utf-8-sig" )

In [10]:
cnpjs = tuple(ode_cam["cnpj_limpo"])

In [11]:
cnpjs_odebrecht = tuple(ode_cam.query("grupo == 'odebrecht'").cnpj_limpo)

In [12]:
cnpjs_camargo = tuple(ode_cam.query("grupo == 'camargo'").cnpj_limpo)

# Baixando dados da RAIS

In [12]:
server = 'beirute-01'

database = 'RAIS'

port= '1433'

username = 'GabrielCP3'

password = '@VN1ai2GG3as4'

driver= '{SQL Server}'

cnxn = pyodbc.connect('DRIVER='+driver+';SERVER='+server+';PORT='+port+';DATABASE='+database+';UID='+username+';PWD='+ password)

cursor = cnxn.cursor()

# Achando CNAES Odebrecht

In [13]:
estados = ["SP","RJ","BA","MG","PR"] # estados de interesse

In [14]:
cnaes = []
df = pd.DataFrame()

In [15]:
def cnae(ano,estado):
    global df, cnaes
    consulta_1 = """ SELECT
                 a.CPF,
                 a.[Nome Trabalhador],
                 a.[Município],
                 a.[CNAE 95 Classe],
                 a.[Sexo Trabalhador],
                 a.[Raça Cor],
                 a.[Idade],
                 a.[CNPJ Raiz],
                 a.[CBO Ocupação 2002],
                 a.[CNAE 2 0 Classe] as cnae,
                 a.[Vl Salário Contratual],
                 a.[Vl Remun Média (SM)],
                 a.[Vl Remun Média Nom],
                 a.[Vl Remun Dezembro Nom],
                 a.[Tipo Vínculo],
                 a.[Motivo Desligamento],
                 a.[Mês Desligamento],
                 a.[Escolaridade após 2005],
                 a.[Natureza Jurídica],
                 a.[Data Admissão Declarada],
                 a.[Tempo Emprego],
                 a.[CNAE 2 0 Subclasse] as cnae_sub,
                 a.[Vínculo Ativo 31 12] as vinc_ativ3112
                 FROM dbo.{}{}ID a
                 WHERE a.[Escolaridade após 2005] >= 7
                 AND [CNPJ Raiz] IN {}
                """.format(estado,ano,cnpjs_odebrecht)

    df_provisorio = pd.read_sql(consulta_1,  cnxn)

    print(df_provisorio["vinc_ativ3112"].unique())
    cnaes = list(dict.fromkeys(cnaes + list(df_provisorio.cnae.unique())))

In [16]:
start_time = time.time()

for x in estados:
    cnae(2015,x)

print("My program took", time.time() - start_time, "to run")

[1 0]
[1 0]
[1 0]
[0 1]
[1 0]
My program took 24.90180802345276 to run


In [17]:
lista = []
for i in cnaes:
    lista.append(i[0:5])

In [18]:
cnaes = tuple(lista)

In [19]:
cnaes

('42120',
 '20215',
 '72100',
 '36006',
 '71120',
 '64620',
 '70204',
 '19314',
 '20312',
 '52311',
 '52214',
 '37011',
 '41204',
 '42138',
 '66223',
 '38211',
 '42227',
 '42928',
 '73122',
 '52401',
 '49124',
 '41107',
 '46931',
 '09106',
 '33171',
 '52508',
 '10651',
 '38220',
 '01351',
 '37029',
 '20118',
 '25993',
 '46893')

In [20]:
len(cnaes)

33

## Criando Painel 2012

In [ ]:
estados = ["SP","RJ","BA","MG","PR"] # estados de interesse
anos = [2012,2013,2014] # anos do painel

In [ ]:
cpfs = []
df = pd.DataFrame()

In [ ]:
def raispainel(ano,estado):
    global df, cpfs
    consulta_1 = """ SELECT
                 a.CPF,
                 a.[Nome Trabalhador],
                 a.[Município],
                 a.[CNAE 95 Classe],
                 a.[Sexo Trabalhador],
                 a.[Raça Cor],
                 a.[Idade],
                 a.[CNPJ Raiz],
                 a.[CBO Ocupação 2002] as cbo2002,
                 a.[CBO 94 Ocupação] as cbo_94,
                 a.[CNAE 2 0 Classe] as cnae,
                 a.[Vl Salário Contratual],
                 a.[Vl Remun Média (SM)],
                 a.[Vl Remun Média Nom],
                 a.[Vl Remun Dezembro Nom],
                 a.[Tipo Vínculo],
                 a.[Motivo Desligamento],
                 a.[Mês Desligamento],
                 a.[Escolaridade após 2005],
                 a.[Natureza Jurídica],
                 a.[Data Admissão Declarada],
                 a.[Tempo Emprego],
                 a.[CNAE 2 0 Subclasse] as cnae_sub,
                 a.[Vínculo Ativo 31 12] as vinc_ativ3112
                 FROM dbo.{}{}ID a
                 WHERE a.[Escolaridade após 2005] >= 7
                 AND a.[Vínculo Ativo 31 12] != '1'
                 AND a.[Vínculo Ativo 31 12] != ' 1'
                 AND a.[Vínculo Ativo 31 12] != 1
                 AND a.[CNAE 2 0 Classe] IN {}
                """.format(estado,ano,cnaes)

    df_provisorio = pd.read_sql(consulta_1,  cnxn)

    df_provisorio["Ano"] = ano
    df_provisorio["Estado"] = estado
    df_provisorio["painel"] = anos[0]
    
    
    df_provisorio['CPF'] = df_provisorio['CPF'].str.strip()

    
    df_provisorio.loc[(df_provisorio['vinc_ativ3112'] == ' 1') |
                      (df_provisorio['vinc_ativ3112'] == '1')  |
                      (df_provisorio['vinc_ativ3112'] == 'True'), 'vinc_ativ3112'] = 1
    
    df_provisorio.loc[(df_provisorio['vinc_ativ3112'] == ' 0') |
                      (df_provisorio['vinc_ativ3112'] == '0')  |
                      (df_provisorio['vinc_ativ3112'] == 'False'),'vinc_ativ3112'] = 0
    
    df = pd.concat([df, df_provisorio])


    cpfs = list(dict.fromkeys(cpfs + list(df_provisorio.query("vinc_ativ3112 != 1").CPF.unique())))


    print(f"foi criado um df de tamanho {len(df)} e uma lista chamada cpf de tamanho {len(cpfs)}")

In [ ]:

start_time = time.time()

for x in estados:
    raispainel(anos[0],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
df["vinc_ativ3112"].unique()

In [ ]:
def raispainel2(ano,estado):
    global df
    consulta_1 = """ SELECT
                 a.CPF,
                 a.[Nome Trabalhador],
                 a.[Município],
                 a.[CNAE 95 Classe],
                 a.[Sexo Trabalhador],
                 a.[Raça Cor],
                 a.[Idade],
                 a.[CNPJ Raiz],
                 a.[CBO Ocupação 2002] as cbo2002,
                 a.[CBO 94 Ocupação] as cbo_94,
                 a.[CNAE 2 0 Classe] as cnae,
                 a.[Vl Salário Contratual],
                 a.[Vl Remun Média (SM)],
                 a.[Vl Remun Média Nom],
                 a.[Vl Remun Dezembro Nom],
                 a.[Tipo Vínculo],
                 a.[Motivo Desligamento],
                 a.[Mês Desligamento],
                 a.[Escolaridade após 2005],
                 a.[Natureza Jurídica],
                 a.[Data Admissão Declarada],
                 a.[Tempo Emprego],
                 a.[CNAE 2 0 Subclasse] as cnae_sub,
                 a.[Vínculo Ativo 31 12] as vinc_ativ3112
                 FROM dbo.{}{}ID a
                 WHERE a.[Vínculo Ativo 31 12] != '0'
                 AND a.[Vínculo Ativo 31 12] != ' 0'
                 AND a.[Vínculo Ativo 31 12] != 0
                 AND a.[Vínculo Ativo 31 12] != ''
                 AND a.[Escolaridade após 2005] >= 7
                """.format(estado,ano)

    df_provisorio = pd.read_sql(consulta_1,  cnxn)
    
    df_provisorio['CPF'] = df_provisorio['CPF'].str.strip()
    
    df_provisorio = df_provisorio.query("CPF in @cpfs")
    
    df_provisorio["Ano"] = ano
    df_provisorio["Estado"] = estado
    df_provisorio["painel"] = anos[0]
    
    df = pd.concat([df, df_provisorio])


    print(f"foi criado um df de tamanho {len(df)}")

In [ ]:

start_time = time.time()

for x in estados:
    raispainel2(anos[1],x)
    raispainel2(anos[2],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
df.info()

In [ ]:
df["vinc_ativ3112"].unique()

# Criando painel 2013

In [ ]:
estados = ["SP","RJ","BA","MG","PR"] # estados de interesse
anos = [2013,2014,2015] # anos do painel

cpfs = []

In [ ]:
start_time = time.time()

for x in estados:
    raispainel(anos[0],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
start_time = time.time()

for x in estados:
    raispainel2(anos[1],x)
    raispainel2(anos[2],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
df.info()

In [ ]:
df.painel.unique()

# Criando painel 2014

In [ ]:
estados = ["SP","RJ","BA","MG","PR"] # estados de interesse
anos = [2014,2015,2016] # anos do painel

cpfs = []

In [ ]:
start_time = time.time()

for x in estados:
    raispainel(anos[0],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
start_time = time.time()

for x in estados:
    raispainel2(anos[1],x)
    raispainel2(anos[2],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
df.info()

In [ ]:
df.painel.unique()

# Criando painel 2015

In [ ]:
estados = ["SP","RJ","BA","MG","PR"] # estados de interesse
anos = [2015,2016,2017] # anos do painel

cpfs = []

In [ ]:
start_time = time.time()

for x in estados:
    raispainel(anos[0],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
start_time = time.time()

for x in estados:
    raispainel2(anos[1],x)
    raispainel2(anos[2],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
df.info()

In [ ]:
df.painel.unique()

# Criando painel 2016

In [ ]:
estados = ["SP","RJ","BA","MG","PR"] # estados de interesse
anos = [2016,2017,2018] # anos do painel

cpfs = []

In [ ]:
start_time = time.time()

for x in estados:
    raispainel(anos[0],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
start_time = time.time()

for x in estados:
    raispainel2(anos[1],x)
    raispainel2(anos[2],x)

print("My program took", time.time() - start_time, "to run")

In [ ]:
df.info()

In [ ]:
df.painel.unique()

## Criando variável "cnae_odebrecht_2015"

In [ ]:
df["cnae"] = df["cnae"].apply(lambda x: str(x)[0:5])

In [ ]:
df["cnae"].head()

In [ ]:
df["cnae_odebrecht_2015"] = df["cnae"].apply(lambda x: 1 if x in cnaes else 0)

## Criando variável "stem_job"

In [ ]:
cbos_stem = "1223 1236 1237 1413 1425 1426 2011 2012 2021 2030 2031 2032 2033 2034 2111 2112 2122 2123 2124 2131 2132 2133 2134 2140 2142 2143 2144 2145 2146 2147 2148 2149 2211 2212 2221 2222 2341 2342 2343 2344 2513 3001 3003 3011 3012 3111 3112 3115 3121 3122 3123 3161 3171 3172 3180 3181 3182 3183 3185 3186 3187 3201 3212 3253 3951"

- fonte: Machado et all 2021

In [ ]:
cbos_stem = tuple(cbos_stem.split(" "))

In [ ]:
df["stem_job"] = df["cbo2002"].apply(lambda x: 1 if x[0:4] in cbos_stem else 0)

## Criando variável "stem_job_2015"

In [ ]:
cpfs_stem_2015 = df[(df["stem_job"] == 1) & (df["Ano"] == 2015)].CPF.unique()

In [ ]:
df["stem_job_2015"] = df["CPF"].apply(lambda x: 1 if x in cpfs_stem_2015 else 0)

In [ ]:
df.query("stem_job_2015 == 1").Ano.unique()

In [ ]:
len(df.query("stem_job_2015 == 1 & Ano != 2015"))

## Criando variável "odebrecht"

In [ ]:
cnpjs_odebrecht = tuple(ode_cam.query("grupo == 'odebrecht'").cnpj_limpo)

In [ ]:
df["odebrecht"] = df["CNPJ Raiz"].apply(lambda x: 1 if x in cnpjs_odebrecht else 0)

In [ ]:
df.query("odebrecht == 1").head().T

## Criando variável "odebrecht_2015"

In [ ]:
cpfs_odebrecht = df[(df["odebrecht"] == 1) & (df["Ano"] == 2015)].CPF.unique()

In [ ]:
df["odebrecht_2015"] = df["CPF"].apply(lambda x: 1 if x in cpfs_odebrecht else 0)

In [ ]:
df.query("odebrecht_2015 == 1").Ano.unique()

In [ ]:
len(df.query("odebrecht_2015 == 1 & Ano == 2015"))

## Saving

In [ ]:
df.loc[(df['vinc_ativ3112'] == ' 1') |
       (df['vinc_ativ3112'] == '1')  |
       (df['vinc_ativ3112'] == 'True'), 'vinc_ativ3112'] = 1

In [ ]:
df["vinc_ativ3112"].unique()

In [ ]:
df.to_csv("Dados/Output/220517_all_panel_cnae.csv", sep = ";", index = False, encoding = "utf-8-sig")

# Abrindo e Limpando a Base

In [22]:
df = pd.read_csv("Dados/Output/220517_all_panel_cnae.csv", sep = ";", dtype = {'CPF': str, 'CNPJ Raiz': str, 'CBO Ocupação 2002': str, 'Data Admissão Declarada': str, 'cnae': str, "Vínculo Ativo 31 12": str})

In [23]:
len(df.CPF.unique())

2440241

In [24]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5152105 entries, 0 to 5152104
Data columns (total 32 columns):
 #   Column                   Dtype  
---  ------                   -----  
 0   CPF                      object 
 1   Nome Trabalhador         object 
 2   Município                int64  
 3   CNAE 95 Classe           int64  
 4   Sexo Trabalhador         int64  
 5   Raça Cor                 int64  
 6   Idade                    int64  
 7   CNPJ Raiz                object 
 8   cbo2002                  object 
 9   cbo_94                   object 
 10  cnae                     object 
 11  Vl Salário Contratual    float64
 12  Vl Remun Média (SM)      float64
 13  Vl Remun Média Nom       float64
 14  Vl Remun Dezembro Nom    float64
 15  Tipo Vínculo             int64  
 16  Motivo Desligamento      int64  
 17  Mês Desligamento         int64  
 18  Escolaridade após 2005   int64  
 19  Natureza Jurídica        int64  
 20  Data Admissão Declarada  object 
 21  Tempo Em

In [25]:
len(df[df["vinc_ativ3112"] == 1])

1951016

In [26]:
len(df[df["vinc_ativ3112"] == True])

1951016

In [27]:
df["vinc_ativ3112"].unique()

array([0, 1, '1', 'True', 'False'], dtype=object)

In [28]:
df.loc[(df['vinc_ativ3112'] == ' 1') |
       (df['vinc_ativ3112'] == '1')  |
       (df['vinc_ativ3112'] == 'True'), 'vinc_ativ3112'] = 1

In [29]:
df.loc[(df['vinc_ativ3112'] == ' 0') |
       (df['vinc_ativ3112'] == '0')  |
       (df['vinc_ativ3112'] == 'False'), 'vinc_ativ3112'] = 0

In [30]:
df["vinc_ativ3112"].unique()

array([0, 1], dtype=object)

In [31]:
df['cbo2002'] = df['cbo2002'].str.replace('\W', '')

In [32]:
df.rename(columns={"painel": "coorte"}, inplace = True)

In [33]:
df["cnae"] = df["cnae"].apply(lambda x: str(x)[0:5])

In [34]:
df.head().T

0  \
CPF                                                            21827242817   
Nome Trabalhador         MARIA BETANIA MELO RAMOS                      ...   
Município                                                           355030   
CNAE 95 Classe                                                       51918   
Sexo Trabalhador                                                         2   
Raça Cor                                                                 8   
Idade                                                                   33   
CNPJ Raiz                                                         50306471   
cbo2002                                                             391115   
cbo_94                                                               {ñ cl   
cnae                                                                 46931   
Vl Salário Contratual                                               1976.0   
Vl Remun Média (SM)                                                   3.45   
Vl Remun Média Nom                                                 2150.84   
Vl Remun Dezembro Nom                                                  0.0   
Tipo Vínculo                                                            10   
Motivo Desligamento                                                     21   
Mês Desligamento                                                        10   
Escolaridade após 2005                                                   7   
Natureza Jurídica                                                     2062   
Data Admissão Declarada                                           02022004   
Tempo Emprego                                                        104.5   
cnae_sub                                                           4693100   
vinc_ativ3112                                                            0   
Ano                                                                   2012   
Estado                                                                  SP   
coorte                                                                2012   
cnae_odebrecht_2015                                                      1   
stem_job                                                                 0   
stem_job_2015                                                            0   
odebrecht                                                                0   
odebrecht_2015                                                           0   

                                                                         1  \
CPF                                                            00969989890   
Nome Trabalhador         ANA MARIA DO PRADO VILELA                     ...   
Município                                                           351570   
CNAE 95 Classe                                                       45217   
Sexo Trabalhador                                                         2   
Raça Cor                                                                 2   
Idade                                                                   52   
CNPJ Raiz                                                         50331313   
cbo2002                                                             411010   
cbo_94                                                               {ñ cl   
cnae                                                                 41204   
Vl Salário Contratual                                               1317.0   
Vl Remun Média (SM)                                                   2.11   
Vl Remun Média Nom                                                  1317.0   
Vl Remun Dezembro Nom                                                  0.0   
Tipo Vínculo                                                            10   
Motivo Desligamento                                                     11   
Mês Desligamento                                                         1   
Escolaridade apó

# Criando Grupos Econômicos

## Criando Dummy "Odebrecht"

In [35]:
cnpjs_odebrecht = tuple(ode_cam.query("grupo == 'odebrecht'").cnpj_limpo)

In [36]:
df["Odebrecht"] = df["CNPJ Raiz"].apply(lambda x: 1 if x in cnpjs_odebrecht else 0)

In [37]:
df.head()

CPF                                   Nome Trabalhador  Município  \
0  21827242817  MARIA BETANIA MELO RAMOS                      ...     355030   
1  00969989890  ANA MARIA DO PRADO VILELA                     ...     351570   
2  93135173887  CELIA MERCEDES PAULINO                        ...     352320   
3  08466881824  FRANCISCA FLORENTINO DE SOUSA                 ...     355220   
4  40067387810  AUDREY CRISTINA MAGRINI CADINE                ...     354070   

   CNAE 95 Classe  Sexo Trabalhador  Raça Cor  Idade CNPJ Raiz cbo2002 cbo_94  \
0           51918                 2         8     33  50306471  391115  {ñ cl   
1           45217                 2         2     52  50331313  411010  {ñ cl   
2           45217                 2         2     56  0         715210  {ñ cl   
3           67202                 2         2     46  0         411005  {ñ cl   
4           45217                 2         2     21  0         717020  {ñ cl   

   ... vinc_ativ3112   Ano  Estado  coorte  cnae_odebrecht_2015  stem_job  \
0  ...             0  2012      SP    2012                    1         0   
1  ...             0  2012      SP    2012                    1         0   
2  ...             0  2012      SP    2012                    1         0   
3  ...             0  2012      SP    2012                    1         0   
4  ...             0  2012      SP    2012                    1         0   

   stem_job_2015  odebrecht  odebrecht_2015  Odebrecht  
0              0          0               0          0  
1              0          0               0          0  
2              0          0               0          0  
3              0          0               0          0  
4              0          0               0          0  

[5 rows x 33 columns]

In [38]:
df.query("Odebrecht == 1")

CPF                                   Nome Trabalhador  \
2093     46115056772  ROBERTO SEABRA DOMINGUES                      ...   
2094     01403076804  JOSE FRANCISCO MELCHIORI BUCCO                ...   
2095     44027567072  ROBERTO HENRY CAMARA                          ...   
2096     15108889852  ANDRE LUIS DE OLIVEIRA LINO                   ...   
2097     08821889840  MARIO ALBERTO BELENTANI DE CARVALHO           ...   
...              ...                                                ...   
5141557  07149538908  ANDERSON BARBOSA MIAN                         ...   
5142580  09430337726  MARCOS VINICIUS BATISTA RIBEIRO               ...   
5142582  09305325971  DIEGO VOLFF RIBEIRO                           ...   
5142736  90703286900  JOAO MARIA CAMARGO                            ...   
5151477  02396315102  JONATHAS SAMUEL ALVES MOREIRA                 ...   

         Município  CNAE 95 Classe  Sexo Trabalhador  Raça Cor  Idade  \
2093        351880           45233                 1         2     58   
2094        351880           45233                 1         2     55   
2095        351880           45233                 1         2     48   
2096        351880           45233                 1         2     39   
2097        355030           45233                 1         2     45   
...            ...             ...               ...       ...    ...   
5141557     410450           45233                 1         8     28   
5142580     410450           45233                 1         8     37   
5142582     410450           45233                 1         8     23   
5142736     410450           45233                 1         8     48   
5151477     410450           45233                 1         2     29   

        CNPJ Raiz cbo2002 cbo_94  ... vinc_ativ3112   Ano  Estado  coorte  \
2093     15102288  214405  {ñ cl  ...             0  2012      SP    2012   
2094     15102288  214405  {ñ cl  ...             0  2012      SP    2012   
2095     15102288  142520  {ñ cl  ...             0  2012      SP    2012   
2096     15102288  214405  {ñ cl  ...             0  2012      SP    2012   
2097     15102288  212405  {ñ cl  ...             0  2012      SP    2012   
...           ...     ...    ...  ...           ...   ...     ...     ...   
5141557  15102288  725205  {ñ cl  ...             1  2018      PR    2016   
5142580  15102288  351605  {ñ cl  ...             1  2018      PR    2016   
5142582  15102288  724315  {ñ cl  ...             1  2018      PR    2016   
5142736  15102288  710215  {ñ cl  ...             1  2018      PR    2016   
5151477  15102288     NaN  {ñ cl  ...             1  2018      PR    2016   

         cnae_odebrecht_2015  stem_job  stem_job_2015  odebrecht  \
2093                       1         1              0          1   
2094                       1         1              0          1   
2095                       1         1              0          1   
2096                       1         1              0          1   
2097                       1         1              0          1   
...                      ...       ...            ...        ...   
5141557                    1         0              0          1   
5142580                    1         0              0          1   
5142582                    1         0              0          1   
5142736                    1         0              0          1   
5151477                    1         0              1          1   

         odebrecht_2015  Odebrecht  
2093                  0          1  
2094                  0          1  
2095                  0          1  
2096                  0          1  
2097                  0          1  
...                 ...        ...  
5141557               0          1  
5142580               0          1  
5142582               0          1  
5142736               0          1  
5151477               0          1  

[82209 rows x 33 columns]

## Criar Dummy Camargo Correa

In [39]:
cnpjs_camargo = tuple(ode_cam.query("grupo == 'camargo'").cnpj_limpo)

In [40]:
df["Camargo"] = df["CNPJ Raiz"].apply(lambda x: 1 if x in cnpjs_camargo else 0)

In [41]:
df.query("Camargo == 1")

CPF                                   Nome Trabalhador  \
2185     81571860991  APARECIDA BENTA DA LUZ IVANOSKI               ...   
2186     33488689808  TATIANE ROSCHEL SANTIAGO                      ...   
2187     30902170821  PATRICIA HELENA GUERINO GOMES HELENO          ...   
2188     35624377819  NATHALI DE GODOI MENK NICOLETTI               ...   
2189     04363065494  MONIQUE ROBERTA SOARES DE ALMEIDA             ...   
...              ...                                                ...   
5112311  07055379601  JEOVA GOMES DOS SANTOS                        ...   
5112312  08649577695  DIEGO VIANA DE SOUZA                          ...   
5112321  07420981680  FLAVIO CORTE DA SILVA                         ...   
5116324  07539972661  FRANCISCO ALVES LARQUER DA COSTA              ...   
5117086  06495211619  ANA FLAVIA OLIVEIRA                           ...   

         Município  CNAE 95 Classe  Sexo Trabalhador  Raça Cor  Idade  \
2185        355030           45233                 2         8     41   
2186        355030           45233                 2         2     26   
2187        350160           45233                 2         2     28   
2188        350160           45233                 2         2     26   
2189        350160           45233                 2         2     28   
...            ...             ...               ...       ...    ...   
5112311     314330           19399                 1         2     34   
5112312     314330           19399                 1         8     31   
5112321     314330           19399                 1         8     35   
5116324     317010           60305                 1         8     31   
5117086     314330           19399                 2         8     35   

        CNPJ Raiz cbo2002 cbo_94  ...   Ano  Estado  coorte  \
2185     61522512  411005  {ñ cl  ...  2012      SP    2012   
2186     61522512  252210  {ñ cl  ...  2012      SP    2012   
2187     61522512  252210  {ñ cl  ...  2012      SP    2012   
2188     61522512  414105  {ñ cl  ...  2012      SP    2012   
2189     61522512  252210  {ñ cl  ...  2012      SP    2012   
...           ...     ...    ...  ...   ...     ...     ...   
5112311  61079117     NaN  {ñ cl  ...  2018      MG    2016   
5112312  61079117     NaN  {ñ cl  ...  2018      MG    2016   
5112321  61079117     NaN  {ñ cl  ...  2018      MG    2016   
5116324  09584935     NaN  {ñ cl  ...  2018      MG    2016   
5117086  61079117     NaN  {ñ cl  ...  2018      MG    2016   

         cnae_odebrecht_2015  stem_job  stem_job_2015  odebrecht  \
2185                       1         0              0          0   
2186                       1         0              0          0   
2187                       1         0              0          0   
2188                       1         0              0          0   
2189                       1         0              0          0   
...                      ...       ...            ...        ...   
5112311                    0         0              0          0   
5112312                    0         0              0          0   
5112321                    0         0              0          0   
5116324                    0         0              0          0   
5117086                    0         0              0          0   

         odebrecht_2015  Odebrecht  Camargo  
2185                  0          0        1  
2186                  0          0        1  
2187                  0          0        1  
2188                  0          0        1  
2189                  0          0        1  
...                 ...        ...      ...  
5112311               0          0        1  
5112312               0          0        1  
5112321               0          0        1  
5116324               0          0        1  
5117086               0          0        1  

[11873 rows x 34 columns]

# Gerando variável "empreendedor"

# Gerando variável "CEO_LT"

- Aqui vou gerar a principal variável de CEO, com base em (Hirakawa et al, 2010)

## Pegar CBOs de "directors" ou "managers"

In [60]:
cbos_1994 = pd.read_csv("Dados/Input/cbo-isco-conc.csv", sep = ",", dtype ='str',  encoding='latin-1')

- Tabela de Marc Muendler disponível em: https://econweb.ucsd.edu/muendler/html/brazil.html#brazoccu
    - Metodologia: (Muendler, 2004, p.16)

In [61]:
cbos_1994 = cbos_1994.dropna()

In [62]:
cbos_1994_managers = cbos_1994.loc[cbos_1994.cbotrans.str.contains('Manager', case = False)]

In [63]:
cbos_1994_directors = cbos_1994.loc[cbos_1994.cbotrans.str.contains('Director', case = False)]

In [64]:
len(cbos_1994_managers)

54

In [65]:
len(cbos_1994_directors)

46

In [66]:
cbos_1994_managers['CBO94'] = cbos_1994_managers['cboid'].str.replace('\W', '')

In [67]:
cbos_1994_directors['CBO94'] = cbos_1994_directors['cboid'].str.replace('\W', '')

## Conversao CBOs 94 para 2002

- Com base em Ricardo Dahis: https://github.com/rdahis/clean_RAIS/tree/master/RAIS/extra/CBO/conversao%2094-02

In [68]:
cbos_2002_managers_directors = pd.read_csv("Dados\Input\CBO94 - CBO2002 - Conversao com 90.csv", sep = ";", dtype ='str')

In [69]:
cbos_2002_managers_directors.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3897 entries, 0 to 3896
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   CBO94    3897 non-null   object
 1   CBO2002  3897 non-null   object
dtypes: object(2)
memory usage: 61.0+ KB


In [70]:
cbos_2002_managers_directors.head()

CBO94 CBO2002
0  X4010  020105
1  X4020  020205
2  X4030  021105
3  X4040  021210
4  X5010  010110

## Juntando bases

In [71]:
cbos_2002_managers = cbos_2002_managers_directors.merge(cbos_1994_managers, on='CBO94', how='inner')

In [72]:
len(cbos_2002_managers)

170

In [73]:
cbos_2002_directors = cbos_2002_managers_directors.merge(cbos_1994_directors, on='CBO94', how='inner')

In [74]:
len(cbos_2002_directors)

80

In [58]:
df["cbo_2002_manager"] = df["cbo2002"].apply(lambda x: 1 if x in list(cbos_2002_managers.CBO2002.unique()) else 0)

KeyboardInterrupt: 

In [ ]:
df.query("cbo_2002_manager == 1").Ano.unique()

In [ ]:
len(df.query("cbo_2002_manager == 1").CPF.unique()) / len(df.CPF.unique())

In [ ]:
df.query("cbo_2002_manager == 1").head().T

In [ ]:
cbos_2002_managers.query("CBO2002 == '411010'")

In [ ]:
df["cbo_2002_director"] = df["cbo2002"].apply(lambda x: 1 if x in list(cbos_2002_directors.CBO2002.unique()) else 0)

In [ ]:
df.query("cbo_2002_director == 1").Ano.unique()

In [ ]:
len(df.query("cbo_2002_director == 1").CPF.unique()) / len(df.CPF.unique())

In [ ]:
df.query("cbo_2002_director == 1").head().T

In [ ]:
cbos_2002_directors.query("CBO2002 == '411010'")

# TODO - Criando variável "new_firm"

In [13]:
df = pd.read_csv("Dados/Output/220517_all_panel_cnae_ceo.csv", sep = ";", dtype = {'CPF': str, 'cnpj': str, 'cbo2002': str, 'Data Admissão Declarada': str, 'cnae': str, "Vínculo Ativo 31 12": str})

In [18]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5152105 entries, 0 to 5152104
Data columns (total 36 columns):
 #   Column                   Dtype  
---  ------                   -----  
 0   CPF                      object 
 1   Nome Trabalhador         object 
 2   Município                int64  
 3   CNAE 95 Classe           int64  
 4   Sexo Trabalhador         int64  
 5   Raça Cor                 int64  
 6   Idade                    int64  
 7   cnpj                     object 
 8   cbo2002                  float64
 9   cbo_94                   object 
 10  cnae                     object 
 11  Vl Salário Contratual    float64
 12  Vl Remun Média (SM)      float64
 13  Vl Remun Média Nom       float64
 14  Vl Remun Dezembro Nom    float64
 15  Tipo Vínculo             int64  
 16  Motivo Desligamento      int64  
 17  Mês Desligamento         int64  
 18  estudo                   int64  
 19  Natureza Jurídica        int64  
 20  Data Admissão Declarada  object 
 21  Tempo Em

## Pegar ano de fundação das empresas na BD+ e dar join

In [14]:
df.rename(columns={"Escolaridade após 2005": "estudo", "CNPJ Raiz": "cnpj"}, inplace = True)

In [57]:
cnpjs = tuple(df[((df["cbo_2002_director"] == 1) | (df["cbo_2002_manager"] == 1)) & (df["vinc_ativ3112"] == 1)].cnpj.unique())

In [58]:
len(cnpjs)

88072

In [43]:
len(cnpjs)

88072

In [60]:
import random

In [71]:
tupla = tuple(random.sample(cnpjs,80000))

In [72]:
len(tupla)

80000

In [73]:
import basedosdados as bd

query = """ SELECT
            cnpj,
            razao_social,
            data_inicio_atividade
            FROM `basedosdados.br_me_socios.empresa` 
            WHERE substring(cnpj,1,8) IN {}
            AND identificador_matriz_filial = '1'
            """.format(tupla)

emp = bd.read_sql(query, billing_project_id= "econometria-314719")

Downloading: 100%|███████████████████████████████████████████████████████████| 79999/79999 [00:10<00:00, 7371.33rows/s]


- Aqui estou considerando que a firma mais antiga é a filial

In [74]:
emp["cnpj"] = emp["cnpj"].str[:-6]

In [75]:
emp.head().T

0  \
cnpj                                                         19848073   
razao_social           Agrocortex Madeiras Do Acre Agroflorestal Ltda   
data_inicio_atividade                             2014-03-07 00:00:00   

                                                  1  \
cnpj                                       08489409   
razao_social           Viacao Vale Do Amazonas Ltda   
data_inicio_atividade           2006-12-05 00:00:00   

                                                         2  \
cnpj                                              05888433   
razao_social           Sabenauto Comercio De Veiculos Ltda   
data_inicio_atividade                  1971-09-09 00:00:00   

                                                        3  \
cnpj                                             05897963   
razao_social           Sigma Transportes E Logistica Ltda   
data_inicio_atividade                 2003-09-23 00:00:00   

                                                                      4  
cnpj                                                           06225625  
razao_social           Goncalves Industria E Comercio De Alimentos Ltda  
data_inicio_atividade                               2004-04-22 00:00:00

In [76]:
len(df)

5152105

In [78]:
df = pd.merge(df,emp[['cnpj','razao_social','data_inicio_atividade']],on='cnpj', how='left')

In [79]:
len(df)

5152105

In [80]:
len(df.query("data_inicio_atividade != 'NaN' & data_inicio_atividade != 'NaT'"))

3444292

In [81]:
df.loc[:, 'cnpj':'data_inicio_atividade'].head(100)

cnpj   cbo2002 cbo_94   cnae  Vl Salário Contratual  \
0   50306471  391115.0  {ñ cl  46931                1976.00   
1   50331313  411010.0  {ñ cl  41204                1317.00   
2   0         715210.0  {ñ cl  41204                 770.00   
3   0         411005.0  {ñ cl  66223                 680.00   
4   0         717020.0  {ñ cl  41204                 622.00   
..       ...       ...    ...    ...                    ...   
95  58580465  214255.0  {ñ cl  71120                6900.00   
96  58580465  262220.0  {ñ cl  71120               40215.36   
97  58580465  410105.0  {ñ cl  71120                7596.34   
98  58580465  214205.0  {ñ cl  71120                8246.40   
99  58580465  123605.0  {ñ cl  71120               17662.07   

    Vl Remun Média (SM)  Vl Remun Média Nom  Vl Remun Dezembro Nom  \
0                  3.45             2150.84                    0.0   
1                  2.11             1317.00                    0.0   
2                  1.23              769.99                    0.0   
3                  1.09              682.59                    0.0   
4                  0.91              570.16                    0.0   
..                  ...                 ...                    ...   
95                 0.00                0.00                    0.0   
96                64.65            40215.36                    0.0   
97                13.65             8492.98                    0.0   
98                14.35             8933.60                    0.0   
99                28.39            17662.06                    0.0   

    Tipo Vínculo  Motivo Desligamento  ...  stem_job  stem_job_2015  \
0             10                   21  ...         0              0   
1             10                   11  ...         0              0   
2             15                   11  ...         0              0   
3             15                   21  ...         0              0   
4             15                   11  ...         0              0   
..           ...                  ...  ...       ...            ...   
95            10                   31  ...         1              0   
96            10                   31  ...         0              0   
97            10                   11  ...         0              0   
98            10                   31  ...         1              0   
99            10                   11  ...         1              1   

    odebrecht odebrecht_2015  Odebrecht  Camargo  cbo_2002_manager  \
0           0              0          0        0                 0   
1           0              0          0        0                 1   
2           0              0          0        0                 0   
3           0              0          0        0                 0   
4           0              0          0        0                 0   
..        ...            ...        ...      ...               ...   
95          0              0          0        0                 0   
96          0              0          0        0                 1   
97          0              0          0        0                 1   
98          0              0          0        0                 0   
99          0              0          0        0                 0   

    cbo_2002_director                                       razao_social  \
0                   0                                                NaN   
1                   0                                                NaN   
2                   0                                                NaN   
3                   0                                                NaN   
4                   0                                                NaN   
..                ...                                                ...   
95                  0  Alumini Engenharia S.A. - Em Recuperacao Judicial   
96                  1  Alumini Engenharia S.A. - Em Recuperacao Judicial   
97                  0  Alumini E

### Criando variável  "admitido_mesmo_ano_criacao"

- Nessa dummy vou colocar = 1 para todos aqueles que foram admitidos dentro de 360 dias da criação da empresa

In [82]:
df['Data Admissão Declarada'] = df['Data Admissão Declarada'].astype('str')

In [83]:
df_datas = list(df["Data Admissão Declarada"])

In [84]:
datas = []
for i in df_datas:
    if len(i) == 7:
        datas.append("0" + i)
    elif len(i) == 6:
        datas.append("00" + i)
    elif len(i) == 5:
        datas.append("000" + i)
    elif len(i) == 4:
        datas.append("0000" + i)
    else:
        datas.append(i)


In [85]:
from datetime import datetime, timedelta

datas_time = []
for s in datas:
    datas_time.append(datetime(year=int(s[4:8]), month=int(s[2:4]), day=int(s[0:2])))

In [86]:
df["data_admissao_empresa"] = datas_time

In [87]:
df["dif_adm_cri"] = df["data_admissao_empresa"] - df["data_inicio_atividade"]

In [88]:
df["dif_adm_cri"] = df["dif_adm_cri"].dt.days

In [89]:
#df["admitido_mesmo_ano_criacao"] = df["dif_adm_cri"].apply(lambda x: 1 if <= 360 else 0)

In [90]:
lista2 = []
for i in df["dif_adm_cri"]:
    if i <= 360:
        lista2.append(1)
    else:
        lista2.append(0)
        
df["admitido_mesmo_ano_criacao"] = lista2

In [91]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5152105 entries, 0 to 5152104
Data columns (total 41 columns):
 #   Column                      Dtype         
---  ------                      -----         
 0   CPF                         object        
 1   Nome Trabalhador            object        
 2   Município                   int64         
 3   CNAE 95 Classe              int64         
 4   Sexo Trabalhador            int64         
 5   Raça Cor                    int64         
 6   Idade                       int64         
 7   cnpj                        object        
 8   cbo2002                     float64       
 9   cbo_94                      object        
 10  cnae                        object        
 11  Vl Salário Contratual       float64       
 12  Vl Remun Média (SM)         float64       
 13  Vl Remun Média Nom          float64       
 14  Vl Remun Dezembro Nom       float64       
 15  Tipo Vínculo                int64         
 16  Motivo Desligament

- antes das alterações eu tinha 52197 observações de "data_inicio_atividade"

In [92]:
len(df.CPF.unique())

2440241

In [94]:
df.head(10).T

0  \
CPF                                                               21827242817   
Nome Trabalhador            MARIA BETANIA MELO RAMOS                      ...   
Município                                                              355030   
CNAE 95 Classe                                                          51918   
Sexo Trabalhador                                                            2   
Raça Cor                                                                    8   
Idade                                                                      33   
cnpj                                                                 50306471   
cbo2002                                                              391115.0   
cbo_94                                                                  {ñ cl   
cnae                                                                    46931   
Vl Salário Contratual                                                  1976.0   
Vl Remun Média (SM)                                                      3.45   
Vl Remun Média Nom                                                    2150.84   
Vl Remun Dezembro Nom                                                     0.0   
Tipo Vínculo                                                               10   
Motivo Desligamento                                                        21   
Mês Desligamento                                                           10   
estudo                                                                      7   
Natureza Jurídica                                                        2062   
Data Admissão Declarada                                              02022004   
Tempo Emprego                                                           104.5   
cnae_sub                                                              4693100   
vinc_ativ3112                                                               0   
Ano                                                                      2012   
Estado                                                                     SP   
coorte                                                                   2012   
cnae_odebrecht_2015                                                         1   
stem_job                                                                    0   
stem_job_2015                                                               0   
odebrecht                                                                   0   
odebrecht_2015                                                              0   
Odebrecht                                                                   0   
Camargo                                                                     0   
cbo_2002_manager                                                            0   
cbo_2002_director                                                           0   
razao_social                                                              NaN   
data_inicio_atividade                                                     NaT   
data_admissao_empresa                                     2004-02-02 00:00:00   
dif_adm_cri                                                               NaN   
admitido_mesmo_ano_criacao                                                  0   

                                                                            1  \
CPF                                                               00969989890   
Nome Trabalhador            ANA MARIA DO PRADO VILELA                     ...   
Município                                                              351570   
CNAE 95 Classe                                                          45217   
Sexo Trabalhador                                                            2   
Raça Cor                                                                    2   
Idade                                                                      52   
cnpj                     

## Criando variável new_firm

In [108]:
df["data_inicio_atividade"].year >= df["coorte"]

True

In [112]:

for i in df["data_inicio_atividade"]:
    print(i.year)

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1966
1966
1969
nan
nan
nan
nan
nan
nan
nan
nan
nan
1966
1966
1966
1966
1966
1966
1966
1966
1966
1966
1966
1966
1966
1966
nan
nan
nan
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
2003
nan
1982
1975
nan
1991
1966
1966
1966
nan
nan
nan
nan
nan
nan
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1982
1977
1982
1968
1982
1977
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1998
nan
nan
nan
nan
nan
nan
2000
2000
2006
2006
2006
2006
2006
2006
2006
nan
nan
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
1982
1971
1971
19

1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
1971
nan
2004
1988
1988
1986
nan
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1988
1988
1988
1988
1988
1988
nan
1988
1988
nan
nan
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
nan
nan
nan
nan
2007
2001
2001
2001
2001
2001
nan
nan
1995
1995
1995
1971
1971
1971
nan
2001
2000
2000
nan
nan
2001
nan
nan
1995
1995
1995
1995
1995
1995
1966
1966
1966
1966
1991
1991
1991
1991
1991
1991
nan
nan
2000
2000
2000
2000
2000
2000
2000
2000
1986
1986
1986
1986
1986
1986
1986
nan
nan
nan
2002
2002
2002
2002
2002
2002
2002
2002
2002
2002
2002
2002
2002
2

1971
1982
nan
nan
nan
1999
1999
1999
1999
1999
1999
1999
1999
1999
1999
1999
1999
1999
1999
1999
1999
1999
1983
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
nan
1995
nan
1995
nan
nan
nan
nan
nan
nan
nan
nan
nan
1995
1995
1995
1992
nan
2012
1996
1996
1996
1996
1996
1996
1996
1996
1996
1996
1996
1996
1996
1996
1996
nan
nan
1986
nan
1999
1999
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1992
1992
nan
nan
nan
1992
1992
1992
nan
nan
2000
nan
nan
nan
nan
nan
nan
nan
nan
nan
2000
2000
2001
2001
nan
nan
nan
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1987
1994
1994
1994
1994
1994
1994
1994
1994
1994
1994
1994
nan
nan
nan
nan
nan
nan
nan
nan
2008
nan
nan
nan
nan
nan
nan
nan
nan
nan
2002
2006
2006
nan
nan
nan
nan
nan
nan
nan
nan
nan
2000
nan
nan
2003
2003
2003
2003
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2004
nan
nan
nan
nan
nan
nan
2006
na

nan
nan
2003
nan
nan
nan
nan
nan
nan
nan
nan
nan
1995
1995
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1987
1987
1985
1985
1985
1985
1985
1985
nan
1987
nan
nan
nan
nan
nan
1999
nan
nan
1995
1995
1995
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2010
nan
nan
nan
nan
1993
1993
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2004
nan
nan
nan
nan
nan
nan
nan
nan
2005
2002
2002
2002
1999
1999
1999
2000
2000
2000
1975
1975
1975
1975
1975
1975
1975
nan
1975
1975
nan
1975
1975
1975
1975
1975
1975
nan
nan
1985
nan
1985
1985
nan
nan
2000
2000
2000
2000
2000
2000
2000
2000
2000
2000
2000
2000
2000
2000
2003
2003
nan
1998
1998
1997
nan
nan
1994
1994
nan
nan
nan
nan
nan
2002
nan
nan
1972
1972
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2003
2003
2003
2003
2003
2003
2003
nan
nan
nan
2005
2005
2005
2005
1994
1994
1994
1994
1994
nan
nan
nan
1994
1994
1993
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2006
2006
200

2000
2000
2000
2000
2000
2000
2000
2000
nan
nan
nan
nan
2000
2000
2000
2000
2000
2000
1986
1986
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1986
2005
nan
nan
1976
nan
nan
1974
1984
1984
nan
1984
1984
nan
nan
1984
1984
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1999
2003
2003
nan
2004
2004
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2001
1978
1978
1982
nan
nan
nan
nan
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
1998
nan
nan
nan
nan
1995
1995
1995
1995
1995
1995
nan
2007
nan
nan
2007
2001
2001
2001
2001
2001
2001
2001
nan
nan
nan
nan
nan
nan
nan
nan
nan
2003
2003
2003
2003
2003
2003
nan
nan
nan
2003
2003
2003
2003
2003
2003
2003
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1998
1998
1998
2003
1972
1972
1972
1972
nan
nan
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
2006
1991
2003
2003
2003
2003
2003
2003
nan
1978
nan
nan
nan
nan


...

nan
2006
2006
2006
2006
nan
2006
nan
nan
nan
nan
nan
nan
nan
1979
1979
1979
1973
1981
1981
1981
1973
1973
1973
1973
1981
1966
1966
1966
1966
1966
1966
1966
nan
1962
1962
1966
1966
1962
nan
nan
nan
nan
1995
1995
1997
1997
1997
1997
1997
1997
1997
1997
1997
1997
1997
nan
1987
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2004
2004
2004
2004
2004
2004
2004
2004
2004
2005
nan
1962
1962
1962
nan
1980
nan
nan
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1981
1981
1972
1973
1981
1981
1981
1981
1973
1973
1973
1973
1973
1981
1981
1981
1981
1981
1972
1972
1981
1981
1981
1973
1972
1981
1981
1981
1972
1973
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
nan
nan
nan
1973
1973
1981
1981
1973
1981
1973
1981
1981
1981
1973
1981
1973
1973
1981
1981
1981
1973
nan
1987
nan
1987
1990
1996
1996
1996
1996
1996
1996
1996
1997

1988
1988
1988
1986
1986
1986
1986
1986
1986
nan
nan
nan
nan
nan
nan
2001
2001
2001
2001
2001
2002
2002
1973
nan
nan
nan
nan
nan
1973
1973
1973
1973
nan
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
nan
nan
nan
nan
1987
1968
1987
nan
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1976
1976
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
1988
2002
2002
2002
2002
2002
2002
2002
1969
nan
nan
nan
nan
nan
2000
nan
2001
2001
1976
1976
1976
nan
1976
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969
1969

2009
2009
2009
2009
2009
2009
nan
nan
2009
2009
2009
2009
2009
2009
2009
2009
2009
2009
2009
2009
2009
2009
2009
2009
2009
nan
nan
nan
nan
nan
1995
1971
1982
1982
1982
1982
1982
1982
1982
1982
1982
1982
1982
1982
1982
1982
1971
1971
nan
nan
1983
1983
1983
nan
2011
1971
nan
1982
1982
1982
1982
1982
1982
1982
1982
2001
2001
2001
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2007
2007
2007
2007
2007
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1973
nan
2002
nan
nan
1986
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
2011
2011
2011
nan
nan
1982
1982
1982
1982
1982
1982
nan
nan
nan
nan
nan
nan
2000
2000
2000
2000
2000
2000
2000
2000
20

nan
2007
1987
1995
nan
nan
nan
nan
nan
nan
nan
nan
2002
2002
2002
2002
2002
nan
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1975
nan
2000
2000
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
2005
2005
2005
2005
2005
2005
2005
2005
2005
2005
2005
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995
1995

KeyboardInterrupt: 

In [116]:
lista2 = []
for i in df["data_inicio_atividade"]:
    for x in df["coorte"]:
        if i.year >= x:
            lista2.append(1)
        else:
            lista2.append(0)
        
df["new_firm"] = lista2

MemoryError: 

In [46]:
len(df.query("new_firm == 1 & (cbo_2002_manager == 1 | cbo_2002_director == 1)").cnpj.unique())

8886

In [47]:
cnpjs = df.query("new_firm == 1 & (cbo_2002_manager == 1 | cbo_2002_director == 1)").cnpj.unique()

- Agora tenho que pegar essas empresas, puxar todos os funcionários delas e selecionar:
    (1) Cargos de "director" (ou se não tiver ver os "manager")
    (2) Dentre esses pegar os top 1 salários *por ano*
    (3) Ver quem da df está dentro da lista de top 1 salário em seu ano

- Com isso posso criar a variável 'manager_director_spinoff'  

## Pegar quem recebeu maiores salários para criar a variável final

In [48]:
anos = [2012,2013,2014,2015,2016,2017,2018] # anos do painel
estados = ["SP","RJ","BA","MG","PR"] # estados de interesse

In [49]:
df_workers = pd.DataFrame()

In [50]:
def raispainel3(ano,estado):
    global df_workers
    consulta_1 = """ SELECT
                 a.CPF,
                 a.[CNPJ Raiz] as cnpj,
                 a.[CBO Ocupação 2002] as cbo2002,
                 a.[Vl Remun Dezembro Nom],
                 a.[Vínculo Ativo 31 12] as vinc_ativ3112
                 FROM dbo.{}{}ID a
                 WHERE a.[Vínculo Ativo 31 12] != '0'
                 AND a.[Vínculo Ativo 31 12] != ' 0'
                 AND a.[Vínculo Ativo 31 12] != 0
                 AND a.[Vínculo Ativo 31 12] != ''
                 AND a.[Escolaridade após 2005] >= 7
                """.format(estado,ano)

    df_provisorio = pd.read_sql(consulta_1,  cnxn)
    
    df_provisorio['cnpj'] = df_provisorio['cnpj'].str.strip()
    
    df_provisorio = df_provisorio.query("cnpj in @cnpjs")
    
    df_provisorio["Ano"] = ano
    df_provisorio["Estado"] = estado
    
    df_workers = pd.concat([df_workers, df_provisorio])


    print(f"foi criado um df de tamanho {len(df_workers)}")

In [51]:

start_time = time.time()

for x in estados:
    raispainel3(anos[0],x)
    raispainel3(anos[1],x)
    raispainel3(anos[2],x)
    raispainel3(anos[3],x)
    raispainel3(anos[4],x)
    raispainel3(anos[5],x)
    raispainel3(anos[6],x)
print("My program took", time.time() - start_time, "to run")

foi criado um df de tamanho 5152105
foi criado um df de tamanho 5152105
foi criado um df de tamanho 5152105
foi criado um df de tamanho 5152105
foi criado um df de tamanho 5152105
foi criado um df de tamanho 5152105
foi criado um df de tamanho 5152105


IndexError: list index out of range

In [53]:
df_workers.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1310990 entries, 208 to 10374678
Data columns (total 7 columns):
 #   Column                 Non-Null Count    Dtype  
---  ------                 --------------    -----  
 0   CPF                    1310990 non-null  object 
 1   cnpj                   1310990 non-null  object 
 2   cbo2002                1310990 non-null  object 
 3   Vl Remun Dezembro Nom  1310990 non-null  float64
 4   vinc_ativ3112          1310990 non-null  int64  
 5   Ano                    1310990 non-null  int64  
 6   Estado                 1310990 non-null  object 
dtypes: float64(1), int64(2), object(4)
memory usage: 80.0+ MB


In [54]:
df_workers.head()

CPF      cnpj cbo2002  Vl Remun Dezembro Nom  vinc_ativ3112  \
208  09487116800  43776517  312210                3927.26              1   
209  06407474850  43776517  724115                 854.23              1   
210  08240847803  43776517  911305                3597.32              1   
211  06268034899  43776517  724115                5418.25              1   
212  01367308844  43776517  411005                   0.00              1   

      Ano Estado  
208  2012     SP  
209  2012     SP  
210  2012     SP  
211  2012     SP  
212  2012     SP

In [75]:
df_workers["cbo_2002_manager"] = df_workers["cbo2002"].apply(lambda x: 1 if x in list(cbos_2002_managers.CBO2002.unique()) else 0)

In [76]:
df_workers["cbo_2002_director"] = df_workers["cbo2002"].apply(lambda x: 1 if x in list(cbos_2002_directors.CBO2002.unique()) else 0)

In [82]:
df_workers = df_workers.dropna()

In [114]:
idx_manager = df_workers.query("cbo_2002_manager == 1 & cbo_2002_director == 0")

In [115]:
idx_manager = idx_manager.groupby(['cnpj','Ano'])['Vl Remun Dezembro Nom'].transform(max) == idx_manager['Vl Remun Dezembro Nom']

In [128]:
df_top_managers = df_workers.query("cbo_2002_manager == 1 & cbo_2002_director == 0")[idx_manager].sort_values(by = ["cnpj","Ano"])

In [135]:

    lista_2012 = df_top_managers[(df_top_managers["Ano"] == 2012)].CPF.unique()
    lista_2013 = df_top_managers[(df_top_managers["Ano"] == 2013)].CPF.unique()
    lista_2014 = df_top_managers[(df_top_managers["Ano"] == 2014)].CPF.unique()
    lista_2015 = df_top_managers[(df_top_managers["Ano"] == 2015)].CPF.unique()
    lista_2016 = df_top_managers[(df_top_managers["Ano"] == 2016)].CPF.unique()
    lista_2017 = df_top_managers[(df_top_managers["Ano"] == 2017)].CPF.unique()
    lista_2018 = df_top_managers[(df_top_managers["Ano"] == 2018)].CPF.unique()

In [136]:
lista_2016

array(['07473876805', '41111990891', '28388390805', ..., '01117565610',
       '12331525803', '35740283850'], dtype=object)

In [163]:
df[(df["CPF"] == "08466881824") & (df["Ano"] == 2012)]["Nome Trabalhador"]

3    FRANCISCA FLORENTINO DE SOUSA                 ...
Name: Nome Trabalhador, dtype: object

In [168]:
df["top_paid_manager"] = df.query("Ano == 2012")["CPF"].apply(lambda x: 1 if x in lista_2012 else 0)

In [170]:
df["top_paid_manager"] = df.query("Ano == 2013")["CPF"].apply(lambda x: 1 if x in lista_2013 else 0)

In [171]:
df["top_paid_manager"] = df.query("Ano == 2014")["CPF"].apply(lambda x: 1 if x in lista_2014 else 0)

In [172]:
df["top_paid_manager"] = df.query("Ano == 2015")["CPF"].apply(lambda x: 1 if x in lista_2015 else 0)

In [173]:
df["top_paid_manager"] = df.query("Ano == 2016")["CPF"].apply(lambda x: 1 if x in lista_2016 else 0)

In [174]:
df["top_paid_manager"] = df.query("Ano == 2017")["CPF"].apply(lambda x: 1 if x in lista_2017 else 0)

In [175]:
df["top_paid_manager"] = df.query("Ano == 2018")["CPF"].apply(lambda x: 1 if x in lista_2018 else 0)

In [176]:
df["top_paid_manager"].unique()

array([nan,  0.,  1.])

In [180]:
df[(df["top_paid_manager"] == 1) & (df["admitido_mesmo_ano_criacao"] == 1)].T

4884075  \
CPF                                                               07171119467   
Nome Trabalhador            JOSE CESAR DE SOUSA                           ...   
Município                                                              354990   
CNAE 95 Classe                                                          45217   
Sexo Trabalhador                                                            1   
Raça Cor                                                                    2   
Idade                                                                      35   
cnpj                                                                 27079713   
cbo2002                                                              715305.0   
cbo_94                                                                  {ñ cl   
cnae                                                                    41204   
Vl Salário Contratual                                             1805.910034   
Vl Remun Média (SM)                                                      2.04   
Vl Remun Média Nom                                                 1951.73999   
Vl Remun Dezembro Nom                                             2026.630005   
Tipo Vínculo                                                               10   
Motivo Desligamento                                                         0   
Mês Desligamento                                                            0   
estudo                                                                      7   
Natureza Jurídica                                                        2135   
Data Admissão Declarada                                              06032017   
Tempo Emprego                                                       21.799999   
cnae_sub                                                              4120400   
vinc_ativ3112                                                               1   
Ano                                                                      2018   
Estado                                                                     SP   
coorte                                                                   2016   
cnae_odebrecht_2015                                                         1   
stem_job                                                                    0   
stem_job_2015                                                               0   
odebrecht                                                                   0   
odebrecht_2015                                                              0   
Odebrecht                                                                   0   
Camargo                                                                     0   
cbo_2002_manager                                                            1   
cbo_2002_director                                                           0   
razao_social                                           C M Manzano Engenharia   
data_inicio_atividade                                     2017-02-09 00:00:00   
cep                                                                  12246002   
data_admissao_empresa                                     2017-03-06 00:00:00   
dif_adm_cri                                                              25.0   
admitido_mesmo_ano_criacao                                                  1   
top_manager                                                                 0   
top_paid_manager                                                          1.0   

                                                                      4884270  \
CPF                                                               03675713580   
Nome Trabalhador            ELIAS DOS SANTOS SANTANA                      ...   
Município                                                              355030   
CNAE 95 Classe                                                          45217   
Sexo Trabalhador   

In [193]:
idx_director = df_workers.query("cbo_2002_director == 1")

In [194]:
idx_director

CPF      cnpj cbo2002  Vl Remun Dezembro Nom  vinc_ativ3112  \
730       17797071500  11245802  710205            6318.490000              1   
731       03846993832  11245802  710205            6715.880000              1   
745       84317388391  11245802  710205           11340.860000              1   
5189      06948839487  09437097  121010            9000.000000              1   
5199      37076051753  09437097  121010           40898.000000              1   
...               ...       ...     ...                    ...            ...   
10369546  27880577840  00063960  141410            4389.660156              1   
10369573  31630915807  00063960  141410               0.000000              1   
10369788  57174245587  00063960  141410            3663.250000              1   
10369795  65880692272  00063960  141410            4378.060059              1   
10369796  98319930553  00063960  141410            3348.550049              1   

           Ano Estado  cbo_2002_manager  cbo_2002_director  
730       2012     SP                 0                  1  
731       2012     SP                 0                  1  
745       2012     SP                 0                  1  
5189      2012     SP                 0                  1  
5199      2012     SP                 0                  1  
...        ...    ...               ...                ...  
10369546  2018     SP                 0                  1  
10369573  2018     SP                 0                  1  
10369788  2018     SP                 0                  1  
10369795  2018     SP                 0                  1  
10369796  2018     SP                 0                  1  

[33732 rows x 9 columns]

In [195]:
idx_director = idx_director.groupby(['cnpj','Ano'])['Vl Remun Dezembro Nom'].transform(max) == idx_director['Vl Remun Dezembro Nom']

In [196]:
idx_director

730         False
731         False
745         False
5189        False
5199        False
            ...  
10369546    False
10369573    False
10369788    False
10369795    False
10369796    False
Name: Vl Remun Dezembro Nom, Length: 33732, dtype: bool

In [197]:
df_top_directors = df_workers.query("cbo_2002_director == 1")[idx_director].sort_values(by = ["cnpj","Ano"])

In [198]:

    lista_2012 = df_top_directors[(df_top_directors["Ano"] == 2012)].CPF.unique()
    lista_2013 = df_top_directors[(df_top_directors["Ano"] == 2013)].CPF.unique()
    lista_2014 = df_top_directors[(df_top_directors["Ano"] == 2014)].CPF.unique()
    lista_2015 = df_top_directors[(df_top_directors["Ano"] == 2015)].CPF.unique()
    lista_2016 = df_top_directors[(df_top_directors["Ano"] == 2016)].CPF.unique()
    lista_2017 = df_top_directors[(df_top_directors["Ano"] == 2017)].CPF.unique()
    lista_2018 = df_top_directors[(df_top_directors["Ano"] == 2018)].CPF.unique()

In [200]:
df["top_paid_director"] = df.query("Ano == 2012")["CPF"].apply(lambda x: 1 if x in lista_2012 else 0)

In [201]:
df["top_paid_director"] = df.query("Ano == 2013")["CPF"].apply(lambda x: 1 if x in lista_2013 else 0)

In [202]:
df["top_paid_director"] = df.query("Ano == 2014")["CPF"].apply(lambda x: 1 if x in lista_2014 else 0)

In [203]:
df["top_paid_director"] = df.query("Ano == 2015")["CPF"].apply(lambda x: 1 if x in lista_2015 else 0)

In [204]:
df["top_paid_director"] = df.query("Ano == 2016")["CPF"].apply(lambda x: 1 if x in lista_2016 else 0)

In [205]:
df["top_paid_director"] = df.query("Ano == 2017")["CPF"].apply(lambda x: 1 if x in lista_2017 else 0)

In [206]:
df["top_paid_director"] = df.query("Ano == 2018")["CPF"].apply(lambda x: 1 if x in lista_2018 else 0)

In [216]:
((df["top_paid_director"] == 1) | (df["top_paid_manager"] == 1)) & (df["admitido_mesmo_ano_criacao"] == 1)

0          False
1          False
2          False
3          False
4          False
           ...  
5152100    False
5152101    False
5152102    False
5152103    False
5152104    False
Length: 5152105, dtype: bool

In [217]:
df["manager_director_spinoff"] = ((df["top_paid_director"] == 1) | (df["top_paid_manager"] == 1)) & (df["new_firm"] == 1)

In [220]:
df[df["manager_director_spinoff"] == 1]

CPF                                   Nome Trabalhador  \
4881755  04106593637  JAIDERSON NUNES DOS SANTOS                    ...   
4882022  02031837893  JOSE SERGIO DOS SANTOS                        ...   
4882661  03782518560  LEANDRO DE JESUS PEIXOTO                      ...   
4884075  07171119467  JOSE CESAR DE SOUSA                           ...   
4884270  03675713580  ELIAS DOS SANTOS SANTANA                      ...   
...              ...                                                ...   
4961469  37621090871  LIVIA CARLA DE SOUZA GONCALVES                ...   
4961585  03232419801  SANDRA FRANCESCON                             ...   
4963022  23381605844  JULIANY ANTUNES D OLIVEIRA                    ...   
4963130  22998518877  CIBELE MARLI DE MELO ALVES                    ...   
4963182  02813419826  SANDRA REGINA CASAROTTO OLIVEIRA LEITE        ...   

         Município  CNAE 95 Classe  Sexo Trabalhador  Raça Cor  Idade  \
4881755     354870           74209                 1         8     41   
4882022     351930           45292                 1         2     60   
4882661     351907           70106                 1         2     32   
4884075     354990           45217                 1         2     35   
4884270     355030           45217                 1         4     31   
...            ...             ...               ...       ...    ...   
4961469     350600           67202                 2         2     29   
4961585     354980           74209                 2         2     56   
4963022     355030           67202                 2         2     25   
4963130     352590           74209                 2         2     34   
4963182     350570           51594                 2         9     55   

             cnpj   cbo2002 cbo_94  ...  \
4881755  28630217       NaN  {ñ cl  ...   
4882022  09608770       NaN  {ñ cl  ...   
4882661  27491739  710205.0  {ñ cl  ...   
4884075  27079713  715305.0  {ñ cl  ...   
4884270  28131473  784205.0  {ñ cl  ...   
...           ...       ...    ...  ...   
4961469  30791525  411010.0  {ñ cl  ...   
4961585  31586261  411010.0  {ñ cl  ...   
4963022  29298921  252105.0  {ñ cl  ...   
4963130  29314741  214215.0  {ñ cl  ...   
4963182  30785882  413110.0  {ñ cl  ...   

                                              razao_social  \
4881755            Ccsn - Consorcio Construtor Sacs Niplan   
4882022                                     Pro Fibra Ltda   
4882661                        Condominio Topazio Spe Ltda   
4884075                             C M Manzano Engenharia   
4884270              E.X.A Prestacao De Servicos -  Eireli   
...                                                    ...   
4961469  M & G Dezotti Administradora E Corretora De Se...   
4961585                              Consorcio Cidade Nova   
4963022  D'or Pme Corretora De Seguros E Servicos Onlin...   
4963130                                Flg Engenharia Ltda   
4963182                      Pp Comercio De Plasticos Ltda   

         data_inicio_atividade       cep  data_admissao_empresa  dif_adm_cri  \
4881755             2017-09-13   9832160             2018-04-26        225.0   
4882022             2008-05-27  14815000             2009-01-22        240.0   
4882661             2017-04-07  13185559             2017-11-23        230.0   
4884075             2017-02-09  12246002             2017-03-06         25.0   
4884270             2017-07-07   3658010             2018-06-18        346.0   
...                        ...       ...                    ...          ...   
4961469             2018-06-26  17016170             2018-11-01        128.0   
4961585             2018-09-24  15025110             2018-12-19         86.0   
4963022             2017-12-20   4551065             2018-04-02        103.0   
4963130             2017-12-22  13211413             2018-06-26        186.0   
4963182             2018-06-26   6408080             2018-08-01         36.0   

         admitid

In [222]:
df[df["CPF"] == "02813419826"].T

2347929  \
CPF                                                               02813419826   
Nome Trabalhador            SANDRA REGINA CASAROTTO DE OLIVEIRA LEIT      ...   
Município                                                              355030   
CNAE 95 Classe                                                          51594   
Sexo Trabalhador                                                            2   
Raça Cor                                                                    2   
Idade                                                                      51   
cnpj                                                                 11150993   
cbo2002                                                              411010.0   
cbo_94                                                                  {ñ cl   
cnae                                                                    46893   
Vl Salário Contratual                                                 5642.46   
Vl Remun Média (SM)                                                      7.87   
Vl Remun Média Nom                                                    5705.74   
Vl Remun Dezembro Nom                                                     0.0   
Tipo Vínculo                                                               10   
Motivo Desligamento                                                        31   
Mês Desligamento                                                           11   
estudo                                                                      9   
Natureza Jurídica                                                        2062   
Data Admissão Declarada                                              16112011   
Tempo Emprego                                                            36.4   
cnae_sub                                                              4689399   
vinc_ativ3112                                                               0   
Ano                                                                      2014   
Estado                                                                     SP   
coorte                                                                   2014   
cnae_odebrecht_2015                                                         1   
stem_job                                                                    0   
stem_job_2015                                                               0   
odebrecht                                                                   0   
odebrecht_2015                                                              0   
Odebrecht                                                                   0   
Camargo                                                                     0   
cbo_2002_manager                                                            1   
cbo_2002_director                                                           0   
razao_social                                 Plt Comercio De Plasticos Eireli   
data_inicio_atividade                                     2009-09-10 00:00:00   
cep                                                                   6408080   
data_admissao_empresa                                     2011-11-16 00:00:00   
dif_adm_cri                                                             797.0   
admitido_mesmo_ano_criacao                                                  0   
top_manager                                                                 1   
top_paid_manager                                                          NaN   
top_paid_director                                                         NaN   
manager_director_spinoff                                                False   

                                                                      2862742  \
CPF                                                               02813419826   
Nome Trabalhador            SANDRA REGINA CASAROTTO DE O LEITE            ...   
Município          

# Salvando

In [223]:
df.to_csv("Dados/Output/220523_all_panel_cnae_ceo.csv", sep = ";", index = False, encoding = "utf-8-sig")

# Criando Tabela Sum Statiscs

- diferenciar por coorte

## Definindo variáveis

In [224]:
def sumstats(ano):
    global tabela
    cpfs_odebrecht = df[(df["Odebrecht"] == 1) & (df["Ano"] == ano)].CPF.unique()
    
    cpfs_camargo = df[(df["Camargo"] == 1) & (df["Ano"] == ano)].CPF.unique()
    
    n_entrepreneur_odebrecht = len(df.query("CPF in @cpfs_odebrecht")[
                                                                      (df["coorte"] == ano) &
                                                                      (df["manager_director_spinoff"] == 1) &
                                                                      (df["Odebrecht"] == 0) &
                                                                      (df["Camargo"] == 0)].CPF.unique())
    n_entrepreneur_camargo = len(df.query("CPF in @cpfs_camargo")[
                                                                  (df["coorte"] == ano) &
                                                                  (df["manager_director_spinoff"] == 1) &
                                                                  (df["Odebrecht"] == 0) &
                                                                  (df["Camargo"] == 0)].CPF.unique())
    
    n_bluecollar_odebrecht = len(df.query("CPF in @cpfs_odebrecht")[(df["manager_director_spinoff"] == 0) &
                                                                    (df["coorte"] == ano) &
                                                                    (df["Odebrecht"] == 0)].CPF.unique())

    n_bluecollar_camargo = len(df.query("CPF in @cpfs_camargo")[(df["manager_director_spinoff"] == 0) &
                                                                (df["coorte"] == ano) &
                                                                (df["Camargo"] == 0)].CPF.unique())
    
    perc_entrepreneur_odebrecht = round((n_entrepreneur_odebrecht / (n_entrepreneur_odebrecht + n_bluecollar_odebrecht))*100, 2) 
    perc_entrepreneur_camargo = round((n_entrepreneur_camargo / (n_entrepreneur_camargo + n_bluecollar_camargo))*100, 2)
    perc_bluecollar_odebrecht = 100 - perc_entrepreneur_odebrecht
    perc_bluecollar_camargo = 100 - perc_entrepreneur_camargo
    
    study_entrepreneur_odebrecht = round(df.query("CPF in @cpfs_odebrecht")[
                                                                            (df["coorte"] == ano) &
                                                                            (df["manager_director_spinoff"] == 1) &
                                                                            (df["Odebrecht"] == 0) &
                                                                            (df["Camargo"] == 0)].estudo.median(),2)
    
    study_entrepreneur_camargo = round(df.query("CPF in @cpfs_camargo")[
                                                                        (df["coorte"] == ano) &
                                                                        (df["manager_director_spinoff"] == 1) &
                                                                        (df["Odebrecht"] == 0) &
                                                                        (df["Camargo"] == 0)].estudo.median(),2)
    
    study_bluecollar_odebrecht = round(df.query("CPF in @cpfs_odebrecht")[(df["manager_director_spinoff"] == 0) &
                                                                          (df["coorte"] == ano) &
                                                                          (df["Odebrecht"] == 0)].estudo.median(),2)
    
    study_bluecollar_camargo = round(df.query("CPF in @cpfs_camargo")[(df["manager_director_spinoff"] == 0) &
                                                                      (df["coorte"] == ano) &
                                                                      (df["Camargo"] == 0)].estudo.median(),2)
    
    age_entrepreneur_odebrecht = round(df.query("CPF in @cpfs_odebrecht")[
                                                                          (df["coorte"] == ano) &
                                                                          (df["manager_director_spinoff"] == 1) &
                                                                          (df["Odebrecht"] == 0) &
                                                                          (df["Camargo"] == 0)].Idade.mean(),2)
     
    age_entrepreneur_camargo = round(df.query("CPF in @cpfs_camargo")[
                                                                      (df["coorte"] == ano) &
                                                                      (df["manager_director_spinoff"] == 1) &
                                                                      (df["Odebrecht"] == 0) &
                                                                      (df["Camargo"] == 0)].Idade.mean(),2)
    
    age_bluecollar_odebrecht = round(df.query("CPF in @cpfs_odebrecht")[(df["manager_director_spinoff"] == 0) &
                                                                        (df["coorte"] == ano) &
                                                                        (df["Odebrecht"] == 0)].Idade.mean(),2)
    
    age_bluecollar_camargo = round(df.query("CPF in @cpfs_camargo")[(df["manager_director_spinoff"] == 0) &
                                                                    (df["coorte"] == ano) &
                                                                    (df["Camargo"] == 0)].Idade.mean(),2)
    
    tenure_entrepreneur_odebrecht_cpfs = df.query("CPF in @cpfs_odebrecht")[
                                                                            (df["coorte"] == ano) &
                                                                            (df["manager_director_spinoff"] == 1) &
                                                                            (df["Odebrecht"] == 0) &
                                                                            (df["Camargo"] == 0)].CPF.unique()
    
    tenure_entrepreneur_odebrecht = round(df.query(f"CPF in @tenure_entrepreneur_odebrecht_cpfs & Ano == {ano} & cnpj in @cnpjs_odebrecht")["Tempo Emprego"].mean(),2)
    
    tenure_bluecollar_odebrecht_cpfs = df.query("CPF in @cpfs_odebrecht")[(df["manager_director_spinoff"] == 0) &
                                                                          (df["coorte"] == ano) &
                                                                          (df["Odebrecht"] == 0)].CPF.unique()
    
    tenure_bluecollar_odebrecht = round(df.query(f"CPF in @tenure_bluecollar_odebrecht_cpfs & Ano == {ano} & cnpj in @cnpjs_odebrecht")["Tempo Emprego"].mean(),2)
    
    tenure_entrepreneur_camargo_cpfs = df.query("CPF in @cpfs_camargo")[
                                                                        (df["coorte"] == ano) &
                                                                        (df["manager_director_spinoff"] == 1) &
                                                                        (df["Odebrecht"] == 0) &
                                                                        (df["Camargo"] == 0)].CPF.unique()
    
    tenure_entrepreneur_camargo = round(df.query(f"CPF in @tenure_entrepreneur_camargo_cpfs & Ano == {ano} & cnpj in @cnpjs_camargo")["Tempo Emprego"].mean(),2)
    
    tenure_bluecollar_camargo_cpfs = df.query("CPF in @cpfs_camargo")[(df["manager_director_spinoff"] == 0) &
                                                                      (df["coorte"] == ano) &
                                                                      (df["Odebrecht"] == 0)].CPF.unique()
    
    tenure_bluecollar_camargo = round(df.query(f"CPF in @tenure_bluecollar_camargo_cpfs & Ano == {ano} & cnpj in @cnpjs_camargo")["Tempo Emprego"].mean(),2)
    
    data = {'Stats_{}'.format(ano): ['N', '%', 'Schooling(median)', 'Age(mean)', 'Tenure(months_mean)'],
        'Entrepreneurs_Odebrecht':[n_entrepreneur_odebrecht, perc_entrepreneur_odebrecht, study_entrepreneur_odebrecht, age_entrepreneur_odebrecht, tenure_entrepreneur_odebrecht],
        'Bluecollar_Odebrecht':[n_bluecollar_odebrecht, perc_bluecollar_odebrecht, study_bluecollar_odebrecht, age_bluecollar_odebrecht, tenure_bluecollar_odebrecht],
        'Entrepreneurs_Camargo':[n_entrepreneur_camargo, perc_entrepreneur_camargo, study_entrepreneur_camargo, age_entrepreneur_camargo, tenure_entrepreneur_camargo],
        'Bluecollar_Camargo':[n_bluecollar_camargo, perc_bluecollar_camargo, study_bluecollar_camargo, age_bluecollar_camargo, tenure_bluecollar_camargo]}
    
    tabela = pd.DataFrame(data)
    tabela.set_index("Stats_{}".format(ano), inplace = True)
    
    
    print(f"A tabela é referente aos funcionários que deixaram a Odebrecht ou a Camargo Corrêa em {ano} e que até o fim de {ano + 2} criaram novas empresas ('entrepreneurs') ou foram contratados por outras empresas fora do grupo econômico de sua empregadora de {ano} ('blue collar')")
    
    print(tabela)

In [228]:
sumstats(2012)

A tabela é referente aos funcionários que deixaram a Odebrecht ou a Camargo Corrêa em 2012 e que até o fim de 2014 criaram novas empresas ('entrepreneurs') ou foram contratados por outras empresas fora do grupo econômico de sua empregadora de 2012 ('blue collar')
                     Entrepreneurs_Odebrecht  Bluecollar_Odebrecht  \
Stats_2012                                                           
N                                        0.0               5000.00   
%                                        0.0                100.00   
Schooling(median)                        NaN                  7.00   
Age(mean)                                NaN                 33.87   
Tenure(months_mean)                      NaN                 13.88   

                     Entrepreneurs_Camargo  Bluecollar_Camargo  
Stats_2012                                                      
N                                      0.0              836.00  
%                                      0.0        

In [229]:
sumstats(2013)

A tabela é referente aos funcionários que deixaram a Odebrecht ou a Camargo Corrêa em 2013 e que até o fim de 2015 criaram novas empresas ('entrepreneurs') ou foram contratados por outras empresas fora do grupo econômico de sua empregadora de 2013 ('blue collar')
                     Entrepreneurs_Odebrecht  Bluecollar_Odebrecht  \
Stats_2013                                                           
N                                        0.0               5326.00   
%                                        0.0                100.00   
Schooling(median)                        NaN                  7.00   
Age(mean)                                NaN                 34.57   
Tenure(months_mean)                      NaN                 14.45   

                     Entrepreneurs_Camargo  Bluecollar_Camargo  
Stats_2013                                                      
N                                      0.0              768.00  
%                                      0.0        

In [230]:
sumstats(2014)

A tabela é referente aos funcionários que deixaram a Odebrecht ou a Camargo Corrêa em 2014 e que até o fim de 2016 criaram novas empresas ('entrepreneurs') ou foram contratados por outras empresas fora do grupo econômico de sua empregadora de 2014 ('blue collar')
                     Entrepreneurs_Odebrecht  Bluecollar_Odebrecht  \
Stats_2014                                                           
N                                        0.0               4948.00   
%                                        0.0                100.00   
Schooling(median)                        NaN                  7.00   
Age(mean)                                NaN                 34.99   
Tenure(months_mean)                      NaN                 13.09   

                     Entrepreneurs_Camargo  Bluecollar_Camargo  
Stats_2014                                                      
N                                      0.0             1431.00  
%                                      0.0        

In [231]:
sumstats(2015)

A tabela é referente aos funcionários que deixaram a Odebrecht ou a Camargo Corrêa em 2015 e que até o fim de 2017 criaram novas empresas ('entrepreneurs') ou foram contratados por outras empresas fora do grupo econômico de sua empregadora de 2015 ('blue collar')
                     Entrepreneurs_Odebrecht  Bluecollar_Odebrecht  \
Stats_2015                                                           
N                                        0.0               4351.00   
%                                        0.0                100.00   
Schooling(median)                        NaN                  7.00   
Age(mean)                                NaN                 35.55   
Tenure(months_mean)                      NaN                 20.82   

                     Entrepreneurs_Camargo  Bluecollar_Camargo  
Stats_2015                                                      
N                                      0.0              482.00  
%                                      0.0        

In [232]:
sumstats(2016)

A tabela é referente aos funcionários que deixaram a Odebrecht ou a Camargo Corrêa em 2016 e que até o fim de 2018 criaram novas empresas ('entrepreneurs') ou foram contratados por outras empresas fora do grupo econômico de sua empregadora de 2016 ('blue collar')
                     Entrepreneurs_Odebrecht  Bluecollar_Odebrecht  \
Stats_2016                                                           
N                                       3.00               3711.00   
%                                       0.08                 99.92   
Schooling(median)                       7.00                  7.00   
Age(mean)                              42.67                 35.93   
Tenure(months_mean)                    23.85                 24.45   

                     Entrepreneurs_Camargo  Bluecollar_Camargo  
Stats_2016                                                      
N                                      0.0               355.0  
%                                      0.0        